In [36]:
# !pip install scipy
#!pip install sentencepiece

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 27.9 MB/s eta 0:00:00


In [22]:
# !pip install --upgrade transformers accelerate


In [22]:
from transformers import VitsModel, AutoTokenizer
import torch

male_model = VitsModel.from_pretrained("facebook/mms-tts-isl")
tokenizer = AutoTokenizer.from_pretrained("facebook/mms-tts-isl")

In [34]:
from transformers import VitsModel, AutoTokenizer
import torch

male_model = VitsModel.from_pretrained("./finetune-hf-vits/rosa/checkpoint-500")
tokenizer = AutoTokenizer.from_pretrained("./finetune-hf-vits/rosa/checkpoint-500")

RuntimeError: Error(s) in loading state_dict for VitsModel:
	size mismatch for text_encoder.embed_tokens.weight: copying a param with shape torch.Size([43, 192]) from checkpoint, the shape in current model is torch.Size([38, 192]).
	You may consider adding `ignore_mismatched_sizes=True` in the model `from_pretrained` method.

In [21]:
from transformers import VitsModel, AutoTokenizer
import torch

female_model = VitsModel.from_pretrained("erlaka/mms-tts-isl-finetuned-dilja")
female_tokenizer = AutoTokenizer.from_pretrained("erlaka/mms-tts-isl-finetuned-dilja")

In [23]:

import scipy.io.wavfile as wav

def save_wav(filename, output, sampling_rate):
    sampling_rate = getattr(sampling_rate, "sampling_rate", 16000)  # Default to 16kHz if not set
    if not (0 <= sampling_rate <= 65535):
        raise ValueError(f"Invalid sampling rate: {sampling_rate}")

    waveform = output.squeeze().cpu().numpy()  # Remove batch dimension if present
    # Convert output to numpy array and scale it
    # waveform = output.squeeze().cpu().numpy()  # Remove batch dimension if present
    # waveform = (waveform * 32767).astype("int16")  # Scale to 16-bit PCM

    # Save waveform to a WAV file
    wav.write(filename, rate=sampling_rate, data=waveform)

In [24]:
def tts(model, tokenizer, text):
    inputs = tokenizer(text, return_tensors="pt")
    with torch.no_grad():
        output = model(**inputs).waveform
    return output

In [33]:

import json
import scipy
from IPython.display import Audio

data = json.loads(open("./show.json").read())


# Find the maximum length of the tensors
for i, segment in enumerate(data[:20]):
    content = segment
    if i % 2 == 0:
        print("Anna: ", end="")
        output = tts(female_model, female_tokenizer, content)
        save_wav(f"output{i}.wav", output, female_model.config.sampling_rate)
    else:
        print("Kári: ", end="")
        output = tts(male_model, male_tokenizer, content)
        save_wav(f"output{i}.wav", output, male_model.config.sampling_rate)
    print(content)
    

# merge the audio files
import os
import subprocess

audio_files = " ".join([f"output{i}.wav" for i in range(len(data[:20]))])


subprocess.run(f"sox {audio_files} output.wav", shell=True)
subprocess.run(f"rm {audio_files}", shell=True)

Anna: Hefurðu fylgst með nýju ríkisstjórninni? Það er spennandi að sjá hvernig þau ætla að tækla efnahagsmálin og lækka vextina eins og þau hafa lofað.
Kári: Já, það verður áhugavert. Sérstaklega með þessa áherslu á húsnæðismál. Það er löngu tímabært að þeir taki á því hvernig markaðurinn hefur farið úr böndunum.
Anna: Algjörlega. Ég vona bara að þetta verði ekki enn ein skammtímalausnin. Það þarf róttækar breytingar ef við ætlum að koma jafnvægi á markaðinn.
Kári: Þetta er rétt. Það er líka verið að tala um að flytja fleiri opinberar stofnanir út á landsbyggðina. Heldurðu að það gæti hjálpað til við að létta á höfuðborgarsvæðinu?
Anna: Kannski, en það er ekki nóg að flytja störf. Það þarf líka að bæta innviði, eins og skóla og heilsugæslu, svo fólk sé reiðubúið að flytja. Annars verður þetta bara hálfgerð sýndarmennska.
Kári: Já, og ef samgöngur eru ekki bættar, þá er þetta eiginlega dæmt til að mistakast. Fólk þarf að komast auðveldlega á milli staða.
Anna: Akkúrat. Við þurfum líka a

CompletedProcess(args='rm output0.wav output1.wav output2.wav output3.wav output4.wav output5.wav output6.wav output7.wav output8.wav output9.wav output10.wav output11.wav output12.wav output13.wav output14.wav output15.wav output16.wav output17.wav output18.wav output19.wav', returncode=0)

In [19]:
import torch
from transformers import pipeline, AutoTokenizer, AutoModelForCausalLM

# Initialize Variables
model_name = "AI-Sweden-Models/gpt-sw3-356m-instruct"
device = "cuda:0" if torch.cuda.is_available() else "cpu"

# Initialize Tokenizer & Model
text_tokenizer = AutoTokenizer.from_pretrained(model_name)
text_model = AutoModelForCausalLM.from_pretrained(model_name)
text_model.eval()
text_model.to(device)
print("Model Loaded")

def converse(prompt, model, tokenizer):
    prompt = f"""
    <|endoftext|><s>
    User:
    {prompt}
    <s>
    Bot:
    """.strip()

    input_ids = text_tokenizer(prompt, return_tensors="pt")["input_ids"].to(device)

    generated_token_ids = text_model.generate(
        inputs=input_ids,
        max_new_tokens=50,
        do_sample=True,
        temperature=0.6,
        top_p=1,
    )[0]

    generated_text = text_tokenizer.decode(generated_token_ids)

    print(generated_text)
    output = generated_text.split("Bot:")[1].strip().split("User:")[0].split("<s>")[0].strip()  
    print(output)

    return output

print(converse("Hvað er nýjustu fréttirnar?", text_model, text_tokenizer))

KeyboardInterrupt: 

In [26]:
# Use a pipeline as a high-level helper
from transformers import pipeline

pipe = pipeline("text-generation", model="mideind/icelandic-gpt-sw3-6.7b")

KeyboardInterrupt: 

In [ ]:
from IPython.display import Audio

# show audio player for "output.wav"
Audio("output.wav")